## ESADE MIBA Artifitial Intelligence Final Project 
### Team Magic Leap (formerly known as Team WWDC 2017)

#### Team Member: Nancy Xiaowen Jiang, Che-Min Tsai, Lifu Zuo

##### Agenda
1. Define the digital event 
2. Definition of the problem (comment lines will be added later in the following notebooks)
3. Scrap the data
4. Clean the dataset (Including Topic analysis)
5. Identify several types of users using different methods
6. Propose a variable for a selected variable that is easy to explain to a decision-maker
7. Propose a variable for the same selected variable that is as accurate as possible

#### In this notebook, we will cover Part 4

##### Make our data easy to access
In this part, we will reframe the raw data and turn them into easy-to-analyze data, such as word counts, retweet_count. Also, we extended more data from 'entities' and 'users' because they were not perfectly stored and couldn't be analyzed in the raw data frame.

In [1]:
#import basic libraries
%pylab inline
import pandas as pd
import seaborn as sns
pd.set_option('display.max_rows', 30)
import numpy as np
import pymongo

Populating the interactive namespace from numpy and matplotlib


In [2]:
#connect to mongoDB
try:
    #use your database name, user and password here:
    #mongodb://<dbuser>:<dbpassword>@<mlab_url>/<database_name>
    with open("credentials1.txt", 'r', encoding='utf-8') as f:
        [name,password,url,dbname]=f.read().splitlines()
        conn=pymongo.MongoClient("mongodb://{}:{}@{}/{}".format(name,password,url,dbname))
        print ("Connected successfully!!!")
except pymongo.errors.ConnectionFailure as e:
    print ("Could not connect to MongoDB: %s" % e) 

db = conn['aifinalproject_1']
collection = db['Magic_Leap']

Connected successfully!!!


In [3]:
#see how one collection looks like
print(collection.find_one())

{'_id': ObjectId('5a3aba680a41186c500a0776'), 'created_at': 'Wed Dec 20 19:30:22 +0000 2017', 'id': 943564250072657920, 'id_str': '943564250072657920', 'full_text': 'People are freaking out over the @magicleap product that almost no one’s seen yet https://t.co/LrQVipZbDN https://t.co/EvGkj5AM6C', 'truncated': False, 'display_text_range': [0, 105], 'entities': {'hashtags': [], 'symbols': [], 'user_mentions': [{'screen_name': 'magicleap', 'name': 'Magic Leap', 'id': 106109075, 'id_str': '106109075', 'indices': [33, 43]}], 'urls': [{'url': 'https://t.co/LrQVipZbDN', 'expanded_url': 'https://buff.ly/2oXaF49', 'display_url': 'buff.ly/2oXaF49', 'indices': [82, 105]}], 'media': [{'id': 943564247203811329, 'id_str': '943564247203811329', 'indices': [106, 129], 'media_url': 'http://pbs.twimg.com/media/DRg2rwFXkAEBJ89.jpg', 'media_url_https': 'https://pbs.twimg.com/media/DRg2rwFXkAEBJ89.jpg', 'url': 'https://t.co/EvGkj5AM6C', 'display_url': 'pic.twitter.com/EvGkj5AM6C', 'expanded_url': 'https://

In [4]:
#read the csv and create a table

#read the CSV file
data = pd.read_csv("C:/Users/maximjxw/Desktop/AI Final Project/magicleap.csv",index_col = 0)
df = pd.DataFrame(data)

clean_df = df[['created_at','display_text_range','full_text','favorite_count','retweeted_status','retweet_count']]
clean_df.head()

created_at display_text_range  \
0  Wed Dec 20 19:30:22 +0000 2017           [0, 105]   
1  Mon Jan 01 00:16:42 +0000 2018            [0, 73]   
2  Wed Dec 20 19:30:24 +0000 2017           [0, 131]   
3  Wed Dec 20 19:30:13 +0000 2017           [0, 110]   
4  Wed Dec 20 19:30:12 +0000 2017            [0, 87]   

                                           full_text  favorite_count  \
0  People are freaking out over the @magicleap pr...               0   
1  Google’s Magic Leap Just Revealed An Impressiv...               0   
2  RT @magicleap: World, meet Magic Leap One. Mag...               0   
3  After 6 years and $1.9 billion in funding, sec...               0   
4  Here it is, people, the @magicleap One: https:...               0   

                                    retweeted_status  retweet_count  
0                                                NaN              0  
1                                                NaN              0  
2  {'created_at': 'Wed Dec 20 14:01:52 +0000 2017...           1570  
3                                                NaN              0  
4                                                NaN              0

In [5]:
#update the text number
text_number = []
for i in clean_df['display_text_range']:
    text_number.append(i.split(',')[1][:-1])

clean_df['text_number'] = text_number
clean_df = clean_df.drop(['display_text_range'], axis = 1)
clean_df.head(2)

D:\PythonSoftware\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


created_at  \
0  Wed Dec 20 19:30:22 +0000 2017   
1  Mon Jan 01 00:16:42 +0000 2018   

                                           full_text  favorite_count  \
0  People are freaking out over the @magicleap pr...               0   
1  Google’s Magic Leap Just Revealed An Impressiv...               0   

  retweeted_status  retweet_count text_number  
0              NaN              0         105  
1              NaN              0          73

In [6]:
#get all hashtags
allhashtags = []

collection_total = collection.find()

for col in collection_total:
    for i in col['entities']['hashtags']:
        allhashtags.append(i['text'])

#see how them look like
print(allhashtags[:10])

['AR', 'AugmentedReality', 'AR', 'AugmentedReality', 'magicleap', 'Cloud', 'Tech', 'HeyHeyHeyTODAY', 'كلنا_عبدالله_بن_زايد', 'RomaTorino']


In [7]:
#get full text
alltext = []

collection_total = collection.find()

for col in collection_total:
    alltext.append(col['full_text'])

#see how it looks like
print(alltext[:2])

['People are freaking out over the @magicleap product that almost no one’s seen yet https://t.co/LrQVipZbDN https://t.co/EvGkj5AM6C', 'Google’s Magic Leap Just Revealed An Impressive Demo Of Augmented Reality']


In [8]:
#see where are all users from
raw_location = []
location = []
collection_total = collection.find()

for col in collection_total:
    raw_location.append(col['user']['location'])
    if col['user']['location'] != '':
        location.append(col['user']['location'])

print(raw_location[:10])
print(location[:10])

['New York, NY', '', 'Vancouver', 'Baketown California, USA', 'San Francisco, CA', 'Berkeley, CA', 'California USA', 'San Francisco, CA', 'Austin, Texas', '127.0.0.1']
['New York, NY', 'Vancouver', 'Baketown California, USA', 'San Francisco, CA', 'Berkeley, CA', 'California USA', 'San Francisco, CA', 'Austin, Texas', '127.0.0.1', 'Malmö, Sweden']


In [9]:
#merge the location in the dataframe
clean_df['location'] = raw_location
clean_df.head()

created_at  \
0  Wed Dec 20 19:30:22 +0000 2017   
1  Mon Jan 01 00:16:42 +0000 2018   
2  Wed Dec 20 19:30:24 +0000 2017   
3  Wed Dec 20 19:30:13 +0000 2017   
4  Wed Dec 20 19:30:12 +0000 2017   

                                           full_text  favorite_count  \
0  People are freaking out over the @magicleap pr...               0   
1  Google’s Magic Leap Just Revealed An Impressiv...               0   
2  RT @magicleap: World, meet Magic Leap One. Mag...               0   
3  After 6 years and $1.9 billion in funding, sec...               0   
4  Here it is, people, the @magicleap One: https:...               0   

                                    retweeted_status  retweet_count  \
0                                                NaN              0   
1                                                NaN              0   
2  {'created_at': 'Wed Dec 20 14:01:52 +0000 2017...           1570   
3                                                NaN              0   
4                                                NaN              0   

  text_number                  location  
0         105              New York, NY  
1          73                            
2         131                 Vancouver  
3         110  Baketown California, USA  
4          87         San Francisco, CA

In [10]:
#get user description
raw_description = []
description = []
collection_total = collection.find()

for col in collection_total:
    raw_description.append(col['user']['description'])
    if col['user']['description'] != '':
        description.append(col['user']['description'])

print(raw_description[:2])
print(description[:2])

clean_df['user_description'] = raw_description

['Official Twitter feed for the Fast Company business media brand;  inspiring readers to think beyond traditional boundaries & create the future of business.', "Hey,I'm ohd Zulhelmi,1,Alor Sear,Kedah"]
['Official Twitter feed for the Fast Company business media brand;  inspiring readers to think beyond traditional boundaries & create the future of business.', "Hey,I'm ohd Zulhelmi,1,Alor Sear,Kedah"]


In [11]:
#get 'followers_count', 'friends_count', 'listed_count', 'created_at', 'favourites_count' & 'statuses_count'
raw_followers_count = []
raw_friends_count = []
raw_listed_count = []
raw_created_at = []
raw_favourites_count = []
raw_statuses_count = []

collection_total = collection.find()

for col in collection_total:
    raw_followers_count.append(col['user']['followers_count'])
    raw_friends_count.append(col['user']['friends_count'])
    raw_listed_count.append(col['user']['listed_count'])
    raw_created_at.append(col['user']['created_at'])
    raw_favourites_count.append(col['user']['favourites_count'])
    raw_statuses_count.append(col['user']['statuses_count'])
    
print(raw_followers_count[:2],
raw_friends_count[:2],
raw_listed_count[:2],
raw_created_at[:2],
raw_favourites_count[:2],
raw_statuses_count[:2])

[2323200, 0] [4026, 128] [44594, 0] ['Wed Mar 28 22:39:21 +0000 2007', 'Sun Dec 03 21:11:06 +0000 2017'] [7814, 1] [174691, 9]


In [12]:
#add user detail to the dataframe
clean_df['user_followers'] = raw_followers_count
clean_df['user_friends'] = raw_friends_count
clean_df['user_listed'] = raw_listed_count
clean_df['user_created_at'] = raw_created_at
clean_df['user_favourites_count'] = raw_favourites_count
clean_df['user_statuses_number'] = raw_statuses_count

clean_df.head(2)

created_at  \
0  Wed Dec 20 19:30:22 +0000 2017   
1  Mon Jan 01 00:16:42 +0000 2018   

                                           full_text  favorite_count  \
0  People are freaking out over the @magicleap pr...               0   
1  Google’s Magic Leap Just Revealed An Impressiv...               0   

  retweeted_status  retweet_count text_number      location  \
0              NaN              0         105  New York, NY   
1              NaN              0          73                 

                                    user_description  user_followers  \
0  Official Twitter feed for the Fast Company bus...         2323200   
1             Hey,I'm ohd Zulhelmi,1,Alor Sear,Kedah               0   

   user_friends  user_listed                 user_created_at  \
0          4026        44594  Wed Mar 28 22:39:21 +0000 2007   
1           128            0  Sun Dec 03 21:11:06 +0000 2017   

   user_favourites_count  user_statuses_number  
0                   7814                174691  
1                      1                     9

In [13]:
#check retweet status and mark them as '1' if one is a retweet, '0' if one is not a retweet
retweet_yesorno = []
for text in alltext:
    if 'RT ' in text:
        retweet_yesorno.append(1)
    else:
        retweet_yesorno.append(0)

In [14]:
#add this to the dataframe
clean_df['Is_this_a_retweet'] = retweet_yesorno
clean_df.head()

created_at  \
0  Wed Dec 20 19:30:22 +0000 2017   
1  Mon Jan 01 00:16:42 +0000 2018   
2  Wed Dec 20 19:30:24 +0000 2017   
3  Wed Dec 20 19:30:13 +0000 2017   
4  Wed Dec 20 19:30:12 +0000 2017   

                                           full_text  favorite_count  \
0  People are freaking out over the @magicleap pr...               0   
1  Google’s Magic Leap Just Revealed An Impressiv...               0   
2  RT @magicleap: World, meet Magic Leap One. Mag...               0   
3  After 6 years and $1.9 billion in funding, sec...               0   
4  Here it is, people, the @magicleap One: https:...               0   

                                    retweeted_status  retweet_count  \
0                                                NaN              0   
1                                                NaN              0   
2  {'created_at': 'Wed Dec 20 14:01:52 +0000 2017...           1570   
3                                                NaN              0   
4                                                NaN              0   

  text_number                  location  \
0         105              New York, NY   
1          73                             
2         131                 Vancouver   
3         110  Baketown California, USA   
4          87         San Francisco, CA   

                                    user_description  user_followers  \
0  Official Twitter feed for the Fast Company bus...         2323200   
1             Hey,I'm ohd Zulhelmi,1,Alor Sear,Kedah               0   
2  IoT specialist / Investor / Co-Founder / Chief...            1007   
3  I make FREE Creative Commons Dubstep #Greyhat ...           15560   
4  #Video #VFX #Animation #CGI #VR Geek! Curating...             169   

   user_friends  user_listed                 user_created_at  \
0          4026        44594  Wed Mar 28 22:39:21 +0000 2007   
1           128            0  Sun Dec 03 21:11:06 +0000 2017   
2          1231           32  Sun Jun 05 20:55:09 +0000 2011   
3          4199          162  Sat Nov 20 03:40:07 +0000 2010   
4           208          133  Thu Jan 21 17:52:00 +0000 2016   

   user_favourites_count  user_statuses_number  Is_this_a_retweet  
0                   7814                174691                  0  
1                      1                     9                  0  
2                   1567                  4990                  1  
3                  26350                 32491                  0  
4                     77                  1993                  0

In [15]:
#get full text from retweets
retweet_fulltext = []
collection_total = collection.find()

for col in collection_total:
    try:
        retweet_fulltext.append(col['retweeted_status']['full_text'])
    except:
        retweet_fulltext.append(0)

retweet_fulltext[:20]

[0,
 0,
 'World, meet Magic Leap One. Magic Leap One, meet the world. More at: https://t.co/LbHY82tYUC https://t.co/2iXgyPs21K',
 0,
 0,
 0,
 0,
 0,
 'After 6 years and $1.9 billion in funding, secretive startup Magic Leap unveils its product for the first time https://t.co/ehlXYzfH7k https://t.co/oUcm0J0e7r',
 'Google-backed Magic Leap unveils its first augmented reality headset, shipping in 2018 https://t.co/oqodIkovSd https://t.co/xom03oVfpZ',
 0,
 'Magic Leap\'s mystery AR glasses are finally revealed. Aimed at developers and "consumer-creators". Shipping in early 2018. After seven years and $1.9bn funding, it has hyperinflated expectations to beat #AR #wearables https://t.co/qer40W5YGj',
 'If you can’t ship product, ship promises https://t.co/rCNXfGhSEC',
 0,
 0,
 0,
 '$1.9 billion later, Magic Leap’s futuristic headset has the same problem as Microsoft’s HoloLens – Business Insider https://t.co/mm4wq0qHx0',
 0,
 0,
 0]

In [17]:
clean_df['retweet_fulltext'] = retweet_fulltext

In [18]:
clean_df = clean_df.drop(['retweeted_status'], axis = 1)
clean_df.head()

created_at  \
0  Wed Dec 20 19:30:22 +0000 2017   
1  Mon Jan 01 00:16:42 +0000 2018   
2  Wed Dec 20 19:30:24 +0000 2017   
3  Wed Dec 20 19:30:13 +0000 2017   
4  Wed Dec 20 19:30:12 +0000 2017   

                                           full_text  favorite_count  \
0  People are freaking out over the @magicleap pr...               0   
1  Google’s Magic Leap Just Revealed An Impressiv...               0   
2  RT @magicleap: World, meet Magic Leap One. Mag...               0   
3  After 6 years and $1.9 billion in funding, sec...               0   
4  Here it is, people, the @magicleap One: https:...               0   

   retweet_count text_number                  location  \
0              0         105              New York, NY   
1              0          73                             
2           1570         131                 Vancouver   
3              0         110  Baketown California, USA   
4              0          87         San Francisco, CA   

                                    user_description  user_followers  \
0  Official Twitter feed for the Fast Company bus...         2323200   
1             Hey,I'm ohd Zulhelmi,1,Alor Sear,Kedah               0   
2  IoT specialist / Investor / Co-Founder / Chief...            1007   
3  I make FREE Creative Commons Dubstep #Greyhat ...           15560   
4  #Video #VFX #Animation #CGI #VR Geek! Curating...             169   

   user_friends  user_listed                 user_created_at  \
0          4026        44594  Wed Mar 28 22:39:21 +0000 2007   
1           128            0  Sun Dec 03 21:11:06 +0000 2017   
2          1231           32  Sun Jun 05 20:55:09 +0000 2011   
3          4199          162  Sat Nov 20 03:40:07 +0000 2010   
4           208          133  Thu Jan 21 17:52:00 +0000 2016   

   user_favourites_count  user_statuses_number  Is_this_a_retweet  \
0                   7814                174691                  0   
1                      1                     9                  0   
2                   1567                  4990                  1   
3                  26350                 32491                  0   
4                     77                  1993                  0   

                                    retweet_fulltext  
0                                                  0  
1                                                  0  
2  World, meet Magic Leap One. Magic Leap One, me...  
3                                                  0  
4                                                  0

In [19]:
#Now we work on date reframing

#First we check the data type
print(type(clean_df['created_at'][0]))

<class 'str'>


In [20]:
month_dict = {'Jan':1,'Feb':2,'Mar':3,'Apr':4,'May':5,'Jun':6,'Jul':7,'Aug':8,'Sep':9,'Oct':10,'Nov':11,'Dec':12}

In [21]:
#Now organize date and do the time series analysis 
#Also get to know users' seniority on twitter for user analysis
tweet_create_year = []
tweet_create_month = []
tweet_create_day = []
tweet_create_date = []
tweet_create_time = []
for i in clean_df['created_at']:
    year = i[-4:]
    month = i[4:7]
    day = i[8:10]
    time = i[11:20]
    tweet_create_year.append(year)
    tweet_create_month.append(month_dict[month])
    tweet_create_day.append(day)
    date = str(year) + '-' + str(month_dict[month]) + '-' + str(day)
    tweet_create_date.append(date)
    tweet_create_time.append(time)
print(tweet_create_date[0])
print(tweet_create_time[0])

2017-12-20
19:30:22 


In [22]:
clean_df['tweet_create_date'] = tweet_create_date
clean_df['tweet_create_time'] = tweet_create_time
clean_df = clean_df.drop(['created_at'], axis = 1)
clean_df.head()

full_text  favorite_count  \
0  People are freaking out over the @magicleap pr...               0   
1  Google’s Magic Leap Just Revealed An Impressiv...               0   
2  RT @magicleap: World, meet Magic Leap One. Mag...               0   
3  After 6 years and $1.9 billion in funding, sec...               0   
4  Here it is, people, the @magicleap One: https:...               0   

   retweet_count text_number                  location  \
0              0         105              New York, NY   
1              0          73                             
2           1570         131                 Vancouver   
3              0         110  Baketown California, USA   
4              0          87         San Francisco, CA   

                                    user_description  user_followers  \
0  Official Twitter feed for the Fast Company bus...         2323200   
1             Hey,I'm ohd Zulhelmi,1,Alor Sear,Kedah               0   
2  IoT specialist / Investor / Co-Founder / Chief...            1007   
3  I make FREE Creative Commons Dubstep #Greyhat ...           15560   
4  #Video #VFX #Animation #CGI #VR Geek! Curating...             169   

   user_friends  user_listed                 user_created_at  \
0          4026        44594  Wed Mar 28 22:39:21 +0000 2007   
1           128            0  Sun Dec 03 21:11:06 +0000 2017   
2          1231           32  Sun Jun 05 20:55:09 +0000 2011   
3          4199          162  Sat Nov 20 03:40:07 +0000 2010   
4           208          133  Thu Jan 21 17:52:00 +0000 2016   

   user_favourites_count  user_statuses_number  Is_this_a_retweet  \
0                   7814                174691                  0   
1                      1                     9                  0   
2                   1567                  4990                  1   
3                  26350                 32491                  0   
4                     77                  1993                  0   

                                    retweet_fulltext tweet_create_date  \
0                                                  0        2017-12-20   
1                                                  0         2018-1-01   
2  World, meet Magic Leap One. Magic Leap One, me...        2017-12-20   
3                                                  0        2017-12-20   
4                                                  0        2017-12-20   

  tweet_create_time  
0         19:30:22   
1         00:16:42   
2         19:30:24   
3         19:30:13   
4         19:30:12

In [23]:
#Now we do the same trick to user_created_at
user_create_year = []
user_create_month = []
user_create_day = []
user_create_date = []
user_create_time = []
for i in clean_df['user_created_at']:
    year = i[-4:]
    month = i[4:7]
    day = i[8:10]
    time = i[11:20]
    user_create_year.append(year)
    user_create_month.append(month_dict[month])
    user_create_day.append(day)
    date = str(year) + '-' + str(month_dict[month]) + '-' + str(day)
    user_create_date.append(date)
    user_create_time.append(time)
print(user_create_date[0])
print(user_create_time[0])

2007-3-28
22:39:21 


In [24]:
clean_df['user_create_date'] = user_create_date
clean_df['user_create_time'] = user_create_time
clean_df = clean_df.drop(['user_created_at'], axis = 1)
clean_df.head()

full_text  favorite_count  \
0  People are freaking out over the @magicleap pr...               0   
1  Google’s Magic Leap Just Revealed An Impressiv...               0   
2  RT @magicleap: World, meet Magic Leap One. Mag...               0   
3  After 6 years and $1.9 billion in funding, sec...               0   
4  Here it is, people, the @magicleap One: https:...               0   

   retweet_count text_number                  location  \
0              0         105              New York, NY   
1              0          73                             
2           1570         131                 Vancouver   
3              0         110  Baketown California, USA   
4              0          87         San Francisco, CA   

                                    user_description  user_followers  \
0  Official Twitter feed for the Fast Company bus...         2323200   
1             Hey,I'm ohd Zulhelmi,1,Alor Sear,Kedah               0   
2  IoT specialist / Investor / Co-Founder / Chief...            1007   
3  I make FREE Creative Commons Dubstep #Greyhat ...           15560   
4  #Video #VFX #Animation #CGI #VR Geek! Curating...             169   

   user_friends  user_listed  user_favourites_count  user_statuses_number  \
0          4026        44594                   7814                174691   
1           128            0                      1                     9   
2          1231           32                   1567                  4990   
3          4199          162                  26350                 32491   
4           208          133                     77                  1993   

   Is_this_a_retweet                                   retweet_fulltext  \
0                  0                                                  0   
1                  0                                                  0   
2                  1  World, meet Magic Leap One. Magic Leap One, me...   
3                  0                                                  0   
4                  0                                                  0   

  tweet_create_date tweet_create_time user_create_date user_create_time  
0        2017-12-20         19:30:22         2007-3-28        22:39:21   
1         2018-1-01         00:16:42        2017-12-03        21:11:06   
2        2017-12-20         19:30:24         2011-6-05        20:55:09   
3        2017-12-20         19:30:13        2010-11-20        03:40:07   
4        2017-12-20         19:30:12         2016-1-21        17:52:00

In [25]:
clean_df.head(30)

full_text  favorite_count  \
0   People are freaking out over the @magicleap pr...               0   
1   Google’s Magic Leap Just Revealed An Impressiv...               0   
2   RT @magicleap: World, meet Magic Leap One. Mag...               0   
3   After 6 years and $1.9 billion in funding, sec...               0   
4   Here it is, people, the @magicleap One: https:...               0   
5   Fascinating read on the development of the mix...               0   
6   After 6 years and $1.9 billion, secretive star...               0   
7   Here it is, people, the @magicleap One: https:...               0   
8   RT @SAI: After 6 years and $1.9 billion in fun...               0   
9   RT @9to5Google: Google-backed Magic Leap unvei...               0   
10  Magic Leap One: The fabled AR headset is real,...               0   
11  RT @George_CCS: Magic Leap's mystery AR glasse...               0   
12  RT @CaseyNewton: If you can’t ship product, sh...               0   
13  Magic Leap One: The fabled AR headset is real,...               0   
14  @jeffgerstmann Answered just hours ago from th...               1   
15  &lt;&lt;Magic Leap's "field of view" (FOV) is ...               0   
16  RT @OccuWorld: $1.9 billion later, Magic Leap’...               0   
17  Magic Leap Unveiled, But Still Unknown https:/...               0   
18  Magic Leap Unveiled, But Still Unknown https:/...               0   
19  Really hope Magic Leap lives up to the intial ...               0   
20  @magicleap @crecenteb Don't have time to read ...               0   
21  @Korihandy Yea, it does look like Riddick! Som...               1   
22  RT @magicleap: World, meet Magic Leap One. Mag...               0   
23             Magic Leap One https://t.co/tk1scKNV6N               0   
24  RT @magicleap: World, meet Magic Leap One. Mag...               0   
25  RT @RoblemVR: Magic Leap AR Headset Hands-on O...               0   
26  Ok Magic Leap definitely needs to focus group ...               1   
27  RT @JBenet38: Magic Leap finally reveals the A...               0   
28  So Beautifull Song https://t.co/DH5hIyhaYf\n#H...               0   
29  $1.9 billion later, Magic Leap’s futuristic he...               1   

    retweet_count text_number                      location  \
0               0         105                  New York, NY   
1               0          73                                 
2            1570         131                     Vancouver   
3               0         110      Baketown California, USA   
4               0          87             San Francisco, CA   
5               0         154                  Berkeley, CA   
6               0         125                California USA   
7               0          87             San Francisco, CA   
8              18         140                 Austin, Texas   
9              37         140                     127.0.0.1   
10              0         114                                 
11              5         139                 Malmö, Sweden   
12              7          81  Bangalore ↔️ Delhi ↔️ Pilani   
13              0         114                                 
14              0          91                washington, nc   
15              0         267              Dresden, Germany   
16              1         140         Electroencephalograph   
17              0          62                 New York City   
18              0          62                                 
19              0         113                Lagos, Nigeria   
20              0         172                    California   
21              0          77              Portland, Oregon   
22           1570         131                       Toronto   
23              0          38              Bengaluru, India   
24           1570         131                           NYC   
25              4         144                         Tokyo   
26              0          58                  Portland, OR   
27              

In [26]:
clean_df.to_csv("C:/Users/maximjxw/Desktop/AI Final Project/clean_data.csv",encoding = 'utf-8')

##### Now we will do topic analysis
We are implementing two kinds of text analysis:
1. tweet text analysis
2. user description text analysis

Here, we will focus on tweet analysis and user description analysis. They can be done easily in the same way.

In [27]:
import pandas as pd
clean_df = pd.read_csv("C:/Users/maximjxw/Desktop/AI Final Project/clean_data.csv", index_col = 0)

In [28]:
clean_df1 = pd.DataFrame(clean_df)
clean_df1.head()

full_text  favorite_count  \
0  People are freaking out over the @magicleap pr...               0   
1  Google’s Magic Leap Just Revealed An Impressiv...               0   
2  RT @magicleap: World, meet Magic Leap One. Mag...               0   
3  After 6 years and $1.9 billion in funding, sec...               0   
4  Here it is, people, the @magicleap One: https:...               0   

   retweet_count  text_number                  location  \
0              0          105              New York, NY   
1              0           73                       NaN   
2           1570          131                 Vancouver   
3              0          110  Baketown California, USA   
4              0           87         San Francisco, CA   

                                    user_description  user_followers  \
0  Official Twitter feed for the Fast Company bus...         2323200   
1             Hey,I'm ohd Zulhelmi,1,Alor Sear,Kedah               0   
2  IoT specialist / Investor / Co-Founder / Chief...            1007   
3  I make FREE Creative Commons Dubstep #Greyhat ...           15560   
4  #Video #VFX #Animation #CGI #VR Geek! Curating...             169   

   user_friends  user_listed  user_favourites_count  user_statuses_number  \
0          4026        44594                   7814                174691   
1           128            0                      1                     9   
2          1231           32                   1567                  4990   
3          4199          162                  26350                 32491   
4           208          133                     77                  1993   

   Is_this_a_retweet                                   retweet_fulltext  \
0                  0                                                  0   
1                  0                                                  0   
2                  1  World, meet Magic Leap One. Magic Leap One, me...   
3                  0                                                  0   
4                  0                                                  0   

  tweet_create_date tweet_create_time user_create_date user_create_time  
0        2017-12-20         19:30:22         2007-3-28        22:39:21   
1         2018-1-01         00:16:42        2017-12-03        21:11:06   
2        2017-12-20         19:30:24         2011-6-05        20:55:09   
3        2017-12-20         19:30:13        2010-11-20        03:40:07   
4        2017-12-20         19:30:12         2016-1-21        17:52:00

In [29]:
#Define environment & space
#Load package to see logs
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

import os
import tempfile
TEMP_FOLDER = tempfile.gettempdir()
print('Folder "{}" will be used to save temporary dictionary and corpus.'.format(TEMP_FOLDER))

Folder "C:\Users\maximjxw\AppData\Local\Temp" will be used to save temporary dictionary and corpus.


In [30]:
#Let's do a test run
#Load the package corpora from the library gensim
from gensim import corpora

documents = []
for i in clean_df1['full_text']:
    documents.append(i)
print(documents)

D:\PythonSoftware\lib\site-packages\gensim\utils.py:860: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
2018-01-07 19:50:23,826 : INFO : 'pattern' package not found; tag filters are not available for English


['People are freaking out over the @magicleap product that almost no one’s seen yet https://t.co/LrQVipZbDN https://t.co/EvGkj5AM6C', 'Google’s Magic Leap Just Revealed An Impressive Demo Of Augmented Reality', 'RT @magicleap: World, meet Magic Leap One. Magic Leap One, meet the world. More at: https://t.co/LbHY82tYUC https://t.co/2iXgyPs21K', 'After 6 years and $1.9 billion in funding, secretive startup Magic Leap unveils its product for the first time https://t.co/XzWXc7J7Nx', 'Here it is, people, the @magicleap One: https://t.co/i0rhg3sKXW | #AR #AugmentedReality', 'Fascinating read on the development of the mixed-reality Magic Leap. I love reading about clever ways to trick the human brain.    https://t.co/JOySq0WWo6 https://t.co/VueCPgKtap', 'After 6 years and $1.9 billion, secretive startup Magic Leap unveils its smart glasses for first time https://t.co/HlDTMVo7a2', 'Here it is, people, the @magicleap One: https://t.co/LIYgZrPPYE | #AR #AugmentedReality', 'RT @SAI: After 6 years

In [31]:
texts = []

# remove common words and tokenize
stoplist = set('for a of the and to in but still from so rt if is it its are was were after with at | -- - …'.split())
texts = [[word for word in document.lower().split() if word not in stoplist]
         for document in documents]

from pprint import pprint  # pretty-printer
pprint(texts)

[['people',
  'freaking',
  'out',
  'over',
  '@magicleap',
  'product',
  'that',
  'almost',
  'no',
  'one’s',
  'seen',
  'yet',
  'https://t.co/lrqvipzbdn',
  'https://t.co/evgkj5am6c'],
 ['google’s',
  'magic',
  'leap',
  'just',
  'revealed',
  'an',
  'impressive',
  'demo',
  'augmented',
  'reality'],
 ['@magicleap:',
  'world,',
  'meet',
  'magic',
  'leap',
  'one.',
  'magic',
  'leap',
  'one,',
  'meet',
  'world.',
  'more',
  'at:',
  'https://t.co/lbhy82tyuc',
  'https://t.co/2ixgyps21k'],
 ['6',
  'years',
  '$1.9',
  'billion',
  'funding,',
  'secretive',
  'startup',
  'magic',
  'leap',
  'unveils',
  'product',
  'first',
  'time',
  'https://t.co/xzwxc7j7nx'],
 ['here',
  'is,',
  'people,',
  '@magicleap',
  'one:',
  'https://t.co/i0rhg3skxw',
  '#ar',
  '#augmentedreality'],
 ['fascinating',
  'read',
  'on',
  'development',
  'mixed-reality',
  'magic',
  'leap.',
  'i',
  'love',
  'reading',
  'about',
  'clever',
  'ways',
  'trick',
  'human',
  'br

  'just',
  'got',
  'unveiled,',
  'sounds',
  'astonishing.',
  'https://t.co/rxsgk2do5f'],
 ['@magicleap:',
  'world,',
  'meet',
  'magic',
  'leap',
  'one.',
  'magic',
  'leap',
  'one,',
  'meet',
  'world.',
  'more',
  'at:',
  'https://t.co/lbhy82tyuc',
  'https://t.co/2ixgyps21k'],
 ['6',
  'years',
  '$1.9',
  'billion',
  'funding,',
  'secretive',
  'startup',
  'magic',
  'leap',
  'unveils',
  'product',
  'first',
  'time…',
  'https://t.co/i7alwt1f17'],
 ['@businessinsider:',
  '6',
  'years',
  '$1.9',
  'billion',
  'funding,',
  'secretive',
  'startup',
  'magic',
  'leap',
  'unveils',
  'product',
  'first',
  'time',
  'https:/…'],
 ['magic',
  'leap',
  'reveals',
  'smart',
  'glasses:',
  'photos,',
  'specs',
  'https://t.co/vflqefhson'],
 ['"last',
  'year,',
  'disney’s',
  'lucasfilm',
  'ilmxlab',
  'r&amp;d',
  'unit',
  'announced',
  'strategic',
  'partnership',
  'magic',
  'leap',
  'released',
  'proof-of-concept',
  'video',
  '“star',
  'wars”

 ['@techminock:',
  '7',
  'years',
  '$1.9',
  'billion',
  'raised,',
  '@magicleap',
  'announces',
  'magic',
  'leap',
  'one',
  'https://t.co/ms7igqaljm',
  '#ar',
  '#arvrinedu',
  '#augment…'],
 ['magic',
  'leap',
  'announced!',
  'looks',
  'like',
  'magic?',
  'augmented',
  'reality',
  'https://t.co/7gw5ocgi3b'],
 ['@magicleap:',
  'world,',
  'meet',
  'magic',
  'leap',
  'one.',
  'magic',
  'leap',
  'one,',
  'meet',
  'world.',
  'more',
  'at:',
  'https://t.co/lbhy82tyuc',
  'https://t.co/2ixgyps21k'],
 ['@magicleap:',
  'world,',
  'meet',
  'magic',
  'leap',
  'one.',
  'magic',
  'leap',
  'one,',
  'meet',
  'world.',
  'more',
  'at:',
  'https://t.co/lbhy82tyuc',
  'https://t.co/2ixgyps21k'],
 ['@businessinsider:',
  '6',
  'years',
  '$1.9',
  'billion,',
  'magic',
  'leap',
  'unveils',
  'ar',
  'smart-glasses',
  'https://t.co/07fxg4dzzx',
  'https://t.co/tlhfgx1tb2'],
 ['@9to5google:',
  'google-backed',
  'magic',
  'leap',
  'unveils',
  'first',


  'leap',
  'unveils',
  'ar',
  'smart-glasses',
  'https://t.co/07fxg4dzzx',
  'https://t.co/tlhfgx1tb2'],
 ['magic',
  'leap',
  'one:',
  'super',
  'stealthy',
  'ar',
  'startup',
  'reveals',
  'first',
  'product',
  'via',
  '@producthunt',
  'https://t.co/fy7wjmqv3z',
  'https://t.co/wstqjogeog'],
 ['mysterious', 'magic', 'leap', 'one', 'here', 'https://t.co/4n6bzn3qds'],
 ['✺',
  'magic',
  'leap',
  'unveils',
  'augmented',
  'reality',
  'headset,',
  'said',
  'launch',
  '2018',
  'https://t.co/tzpqsz4c2a'],
 ['@uploadvr:',
  'magic',
  'leap',
  'finally',
  'reveals',
  'vr',
  'headset,',
  'magic',
  'leap',
  'one',
  'https://t.co/ktpw5fibko',
  'https://t.co/nuqehjeo0b'],
 ['@techreview:',
  '.@magicleap—an',
  'augmented-reality',
  'startup',
  'that',
  'has',
  'raised',
  'close',
  '$2',
  'billion',
  'without',
  'even',
  'publicly',
  'demonstrating',
  'product—…'],
 ['welcome', 'magic', 'leap', 'https://t.co/vpr2lbhsbs'],
 ['you',
  'know',
  'that',


  'going',
  'th…'],
 ['@readscoops',
  "here's",
  'another',
  'interesting',
  'post:',
  'https://t.co/tuexb1bhel'],
 ['@magicleap:',
  'world,',
  'meet',
  'magic',
  'leap',
  'one.',
  'magic',
  'leap',
  'one,',
  'meet',
  'world.',
  'more',
  'at:',
  'https://t.co/lbhy82tyuc',
  'https://t.co/2ixgyps21k'],
 ['magic',
  'leap',
  'reveals',
  'smart',
  'glasses:',
  'photos,',
  'specs',
  'business',
  'insider',
  'https://t.co/p7wcnc20sp'],
 ['looks',
  'like',
  '@magicleap',
  'finally',
  'started',
  'lifting',
  'curtain',
  'https://t.co/zd1efp7yvt'],
 ['magic',
  'leap',
  'has',
  'officially',
  'unveiled',
  'mixed',
  'reality',
  'headset,',
  'we’re',
  'getting',
  'a…',
  'https://t.co/d3mqwwwrou',
  '#gadget'],
 ['@thesinghabhi:',
  'magic',
  'leap',
  'unveiled',
  'their',
  'super',
  '#ar',
  'goggles',
  'today.',
  'flashback',
  'remember',
  'this',
  '2015',
  'video',
  'by',
  '#augmentedreality',
  'super',
  'star…'],
 ['@wonderhowto:',
  

...

  '@pete_tnt',
  "i'm",
  'following',
  'magic',
  'leap',
  'more',
  'than',
  'two',
  'years',
  'now',
  'as',
  'they',
  'very',
  'very',
  'discreet,',
  'i',
  "don't",
  'kno…'],
 ['"everything',
  'we',
  'know',
  'about',
  'magic',
  "leap's",
  'mysterious',
  'new',
  'headset',
  'that',
  'cost',
  '$1.9',
  'billion',
  '6',
  'years',
  'create"',
  'https://t.co/cdt7zhdfx7'],
 ['everything',
  'we',
  'know',
  'about',
  'magic',
  "leap's",
  'mysterious',
  'new',
  'headset',
  'that',
  'cost',
  '$1.9',
  'billion',
  '6',
  'years',
  'create',
  'https://t.co/bjfipkesqy',
  'https://t.co/1mrjtkjeet'],
 ['everything',
  'we',
  'know',
  'about',
  'magic',
  "leap's",
  'mysterious',
  'new',
  'headset',
  'that',
  'cost',
  '$1.9',
  'billion',
  '6',
  'years',
  'create',
  'https://t.co/8q4uxfyfmn'],
 ['everything',
  'we',
  'know',
  'about',
  'magic',
  "leap's",
  'mysterious',
  'new',
  'headset',
  'that',
  'cost',
  '$1.9',
  'billion',
  

  'leap',
  '4',
  'years',
  'results',
  'could',
  'be',
  'glimpse',
  'into',
  'future',
  'of…'],
 ['@futurism:',
  'magic',
  'leap',
  'has',
  'finally',
  'revealed',
  'their',
  'long-awaited',
  'glasses!',
  'https://t.co/pr3103jocz'],
 ['@yahoofinance:',
  'there',
  'reasons',
  'be',
  'skeptical',
  'about',
  'magic',
  "leap's",
  'long-awaited',
  'ar',
  'headset',
  '@danielhowley',
  'https://t.co/qsnzx9gfdk',
  'https:…'],
 ['not', 'long', 'now...', 'https://t.co/3ncd4qkyey'],
 ['@yahoofinance:',
  'there',
  'reasons',
  'be',
  'skeptical',
  'about',
  'magic',
  "leap's",
  'long-awaited',
  'ar',
  'headset',
  '@danielhowley',
  'https://t.co/qsnzx9gfdk',
  'https:…'],
 ['@arconaico:',
  'most',
  'mysterious',
  'start-up',
  'ar',
  '#magicleap',
  'industry',
  'has',
  'finally',
  'shown',
  'first',
  'glasses',
  '#augmentedreality.➡️🚀👓',
  'acc…'],
 ['magic', 'leap', 'unveiled,', 'unknown', 'https://t.co/zztl2aail3'],
 ['magic', 'leap', 'unveiled

  'on',
  'https://t.co/qb45mwjgtq',
  '#mr',
  '#ar',
  'https://t.co…'],
 ['@rickking16:',
  'secretive',
  "'mixed",
  "reality'",
  'startup',
  'finally',
  'revealed',
  'what',
  "it's",
  'been',
  'working',
  'on',
  'https://t.co/qb45mwjgtq',
  '#mr',
  '#ar',
  'https://t.co…'],
 ['@rickking16:',
  'secretive',
  "'mixed",
  "reality'",
  'startup',
  'finally',
  'revealed',
  'what',
  "it's",
  'been',
  'working',
  'on',
  'https://t.co/qb45mwjgtq',
  '#mr',
  '#ar',
  'https://t.co…'],
 ['@roblemvr:',
  'magic',
  'leap',
  'demo',
  'exactly',
  'what',
  'ar',
  'startup',
  'didn’t',
  'need',
  'https://t.co/7kif90o6tv',
  '@magicleap',
  'https://t.co/6r7z0tp0yr'],
 ['@rickking16:',
  'secretive',
  "'mixed",
  "reality'",
  'startup',
  'finally',
  'revealed',
  'what',
  "it's",
  'been',
  'working',
  'on',
  'https://t.co/qb45mwjgtq',
  '#mr',
  '#ar',
  'https://t.co…'],
 ['@rickking16:',
  'secretive',
  "'mixed",
  "reality'",
  'startup',
  'finally',
 

  'describe',
  'tech',
  "company's",
  '"hello',
  'world"',
  'moment',
  'https://t.co/a6iozoqc9t'],
 ['listen',
  "@magicleap's",
  'founder',
  'describe',
  'tech',
  "company's",
  '"hello',
  'world"',
  'moment',
  'https://t.co/a6iozoqc9t'],
 ['magic',
  'leap',
  'has',
  'officially',
  'unveiled',
  'mixed',
  'reality',
  'headset,',
  'we’re',
  'getting',
  'very',
  'cyberpunk',
  'vibe',
  'https://t.co/xratxr2s6n'],
 ['@themalia:',
  'an',
  'early',
  'analysis',
  'magic',
  'leap',
  'one',
  'https://t.co/db67tzxawc'],
 ['an', 'early', 'analysis', 'magic', 'leap', 'one', 'https://t.co/db67tzxawc'],
 ['@roblemvr:',
  'magic',
  'leap',
  'demo',
  'exactly',
  'what',
  'ar',
  'startup',
  'didn’t',
  'need',
  'https://t.co/7kif90o6tv',
  '@magicleap',
  'https://t.co/6r7z0tp0yr'],
 ['magic',
  'leap',
  'one:',
  'all',
  'things',
  'we',
  'don’t',
  'know',
  'https://t.co/kwoxwgfhn4'],
 ['@fabot70:',
  '@vinci_digital',
  '#industrial',
  '#iot',
  '#iiot'

  'wagner,',
  'one',
  'world',
  'experts',
  'this',
  'space.',
  'https://t.co/h5a4qqrh3v'],
 ['@csito:',
  'have',
  'you',
  'been',
  'curious',
  'about',
  'what',
  '@magicleap',
  'up',
  'to?',
  "you've",
  'got',
  'half',
  'an',
  'hour',
  'read',
  'this,',
  'you',
  'might',
  'get',
  'better',
  'idea.',
  'may…'],
 ['have',
  'you',
  'been',
  'curious',
  'about',
  'what',
  '@magicleap',
  'up',
  'to?',
  "you've",
  'got',
  'half',
  'an',
  'hour',
  'read',
  'this,',
  'you',
  'might',
  'get',
  'better',
  'idea.',
  'maybe.',
  'https://t.co/lmgk5am3am'],
 ['magic', 'leap', 'unveiled,', 'unknown', 'https://t.co/bdlkyvszgy'],
 ['@cbinsights:',
  "@magicleap's",
  'latest',
  'patent,',
  'identity',
  'security',
  'next',
  '#ar',
  'ambition?',
  'their',
  'longterm',
  'plans',
  'their',
  'secretive',
  'techn…'],
 ['@arconaico:',
  'most',
  'mysterious',
  'start-up',
  'ar',
  '#magicleap',
  'industry',
  'has',
  'finally',
  'shown',
  '

In [32]:
#remove symbols in text & remove all http address
symbols = set(', . # @ ! ? / * % & ( ) - + = | [ ] … ' ' : "'.split())
texts_1 = []

for text in texts:
    text_1 = []
    for word in text:
        if word[0:6] == 'https:':
            #remove this line
            word = word
        elif word[0] in symbols:
            word = word[1:]
            text_1.append(word)
        elif word[-1] in symbols:
            word = word[:-1]
            text_1.append(word)
        else:                
            word = word
            text_1.append(word)
    texts_1.append(text_1)

pprint(texts_1)

[['people',
  'freaking',
  'out',
  'over',
  'magicleap',
  'product',
  'that',
  'almost',
  'no',
  'one’s',
  'seen',
  'yet'],
 ['google’s',
  'magic',
  'leap',
  'just',
  'revealed',
  'an',
  'impressive',
  'demo',
  'augmented',
  'reality'],
 ['magicleap:',
  'world',
  'meet',
  'magic',
  'leap',
  'one',
  'magic',
  'leap',
  'one',
  'meet',
  'world',
  'more',
  'at'],
 ['6',
  'years',
  '$1.9',
  'billion',
  'funding',
  'secretive',
  'startup',
  'magic',
  'leap',
  'unveils',
  'product',
  'first',
  'time'],
 ['here', 'is', 'people', 'magicleap', 'one', 'ar', 'augmentedreality'],
 ['fascinating',
  'read',
  'on',
  'development',
  'mixed-reality',
  'magic',
  'leap',
  'i',
  'love',
  'reading',
  'about',
  'clever',
  'ways',
  'trick',
  'human',
  'brain'],
 ['6',
  'years',
  '$1.9',
  'billion',
  'secretive',
  'startup',
  'magic',
  'leap',
  'unveils',
  'smart',
  'glasses',
  'first',
  'time'],
 ['here', 'is', 'people', 'magicleap', 'one',

  'techcrunch'],
 ['magicleap:',
  'world',
  'meet',
  'magic',
  'leap',
  'one',
  'magic',
  'leap',
  'one',
  'meet',
  'world',
  'more',
  'at'],
 ['rollingstone:',
  'magic',
  'leap',
  'founder',
  'rony',
  'abovitz',
  'talks',
  'about',
  'tech',
  'ambitions',
  'behind',
  'their',
  'new',
  'mixed-reality',
  'goggles'],
 ['imagine',
  'magic',
  'leap',
  'being',
  'able',
  'place',
  'virtual',
  'big',
  'screen',
  'tv',
  'your',
  'house'],
 ['magic', 'leap', 'unveiled', 'unknown', 'yycwalks'],
 ['roblemvr:',
  'magic',
  'leap',
  'founder',
  'secretive',
  'start-up',
  'unveils',
  'mixed-reality',
  'goggles',
  'magicleap',
  'mixedreality',
  'mag…'],
 ['magic',
  'leap',
  'founder',
  'secretive',
  'start-up',
  'unveils',
  'mixed-reality',
  'goggles',
  'exciting',
  'works',
  'fltech',
  'startups'],
 ['18dmedia:',
  'magic',
  'leap',
  'smart',
  'glasses',
  'slated',
  '2018',
  'release',
  'valuewalk'],
 ['wearableguru:',
  'forbes',
  'm

  'every',
  'day'],
 ['lanceulanoff:',
  'i',
  'wonder',
  'how',
  'awesome',
  'magic',
  'leap',
  'would’ve',
  'been',
  'had',
  'been',
  'released',
  'five',
  'or',
  'even',
  'two',
  'years',
  'ago',
  'before',
  'we',
  'tried',
  'sel'],
 ['greendoorlabs:',
  'exciting',
  'looking',
  'forward',
  'hands-on',
  'reviews',
  'hopefully',
  'will',
  'get',
  'try',
  'after',
  '7',
  'years',
  '$1.9',
  'billion',
  'funding,'],
 ['augmentedreality', 'goggles', 'unveiled', 'magicleap'],
 ['magic', 'leap', 'launch', 'augmented', 'reality', 'goggles', '2018'],
 ['magic',
  'leap',
  'says',
  'will',
  'ship',
  'first',
  'augmented',
  'reality',
  'glasses',
  '2018'],
 ['lives', 'prepare', 'uncanny', 'valley'],
 ['mysterious',
  'augmented',
  'reality',
  'firm',
  'magic',
  'leap',
  'reveals',
  'first',
  'headset'],
 ['digital',
  'transformation',
  'digest',
  'google',
  'chrome',
  'ad',
  'block',
  'plan',
  'looms',
  "china's",
  'red-hot',
  'xunle

  'he..'],
 ['6',
  'years',
  '$1.9',
  'billion',
  'secretive',
  'startup',
  'magic',
  'leap',
  'unveils',
  'smart',
  'glasses',
  'first',
  'time'],
 ['big', 'hype', 'magic', 'leap', 'vr', 'goggles'],
 ['you’re', 'seeing', 'future', 'folks'],
 ['monitor_sur',
  'ft',
  'lookingfornews&gt;&gt;&gt;',
  'financial',
  'time',
  'fastft',
  'magic',
  'leap',
  'launch',
  'augmented',
  'reality',
  'goggles',
  '2018',
  'fastft',
  'magic',
  'leap',
  'launch',
  'augmented',
  'reality',
  'goggles',
  '2018'],
 ['antonhand:',
  'googglass',
  'i',
  'look',
  'like',
  'i',
  'had',
  'trouble',
  'introducing',
  'myself',
  'even',
  'before',
  'sticking',
  'camera',
  'your',
  'face',
  'snapglasses',
  'i',
  'look',
  'lik'],
 ['benedictevans:',
  'magic',
  'leap',
  'one',
  'only',
  'handful',
  'genuine',
  "'holy",
  'shit',
  'i',
  "can't",
  'believe',
  "i'm",
  'seeing',
  "this'",
  'moments',
  "i've",
  'had',
  'as',
  'an',
  'adult.'],
 ['magic',
 

 ['magic',
  'leaps',
  'unveils',
  'lightwear',
  'potentially',
  'game-changing',
  'mixed-reality',
  'headset'],
 ['magic',
  'leap',
  'finally',
  'announces',
  'headset',
  "it's",
  'vague',
  'rendered',
  'photoshop',
  'ars',
  'technica'],
 ['magic',
  'leap',
  'finally',
  'reveals',
  'vr',
  'headset',
  'magic',
  'leap',
  'one',
  '',
  'magic',
  'leap'],
 ['‘magic',
  'leap',
  'one',
  'creator',
  'edition’',
  'ar',
  'goggles',
  'could',
  'be',
  'next',
  'internet'],
 ['neilcybart:',
  'magic',
  'leap',
  'just',
  'unveiled',
  'mixed-reality',
  'goggles',
  'oh',
  'my'],
 ['magic', 'leap', 'website', 'on', 'mobile', '🔥😎🔥https://t.co/cnjbtgrzl5'],
 ['magic',
  'leap',
  'finally',
  'unveils',
  'creator',
  'edition',
  'cd-like',
  'power',
  'pack',
  'snapchat-like',
  'goggles',
  'uncertain',
  'future'],
 ['gaming',
  'magic',
  'leap',
  'finally',
  'announces',
  'headset',
  'it’s',
  'vague',
  'rendered',
  'photoshop',
  'enlarge',
  ''

...

  "leap's",
  'mysterious',
  'new',
  'headset',
  'that',
  'cost',
  '$1.9',
  'billion',
  '6',
  'years',
  'create'],
 ['yahoofinance:',
  'magic',
  'leap',
  'worth',
  'billions',
  "i'm",
  'not',
  'sold',
  'on',
  'headset',
  'danielhowley'],
 ['$1.9',
  'billion',
  'later',
  'magic',
  'leap',
  'finally',
  'unveiled',
  'smart',
  'glasses',
  '—',
  "here's",
  'what',
  'we',
  'know'],
 ['businessinsider:',
  '$1.9',
  'billion',
  'later',
  'magic',
  'leap',
  'finally',
  'unveiled',
  'smart',
  'glasses',
  '—',
  "here's",
  'what',
  'we',
  'know'],
 ['businessinsider:',
  '$1.9',
  'billion',
  'later',
  'magic',
  'leap',
  'finally',
  'unveiled',
  'smart',
  'glasses',
  '—',
  "here's",
  'what',
  'we',
  'know'],
 ['businessinsider:',
  '$1.9',
  'billion',
  'later',
  'magic',
  'leap',
  'finally',
  'unveiled',
  'smart',
  'glasses',
  '—',
  "here's",
  'what',
  'we',
  'know'],
 ['businessinsider:',
  '$1.9',
  'billion',
  'later',
  'ma

  'vr/ar',
  'we’ve',
  'been',
  'waiting',
  'thenextweb',
  'ar',
  'vr…'],
 ['magic', 'leap', 'one', 'headset', 'announced', 'cnet', 'news', 'technews'],
 ['last',
  'update',
  '2017',
  'stevenvbe',
  'on',
  'instacart',
  'magic',
  'leap',
  '..',
  'looking',
  'forward',
  'updates',
  '2018',
  'thanks',
  'effort',
  'input',
  'steven'],
 ['thetonicox:',
  'have',
  'courage',
  'leap',
  'outside',
  'your',
  'comfort',
  'zone',
  "that's",
  'magic',
  'happens..',
  'http://t.co/joagemy86i'],
 ['magic', 'leap', 'design', 'sidebar'],
 ['yahoofinance:',
  'there',
  'reasons',
  'be',
  'skeptical',
  'about',
  'magic',
  "leap's",
  'long-awaited',
  'ar',
  'headset',
  'danielhowley'],
 ['6',
  'years',
  '$1.9',
  'billion',
  'secretive',
  'magic',
  'leap',
  'unveils',
  'product',
  'first',
  'time'],
 ['gazecoin:',
  "microsoft's",
  'holonlens',
  'headset',
  'has',
  'some',
  'serious',
  'competition',
  'google-backed',
  'startup',
  'magic',
  'leap

 ['i',
  'can',
  'sense',
  'that',
  'that',
  '$2b',
  'magic',
  'leap',
  'headset',
  'will',
  'feel',
  'shit',
  'considering',
  'on',
  'what',
  'i',
  'can',
  'see',
  'right',
  'now',
  'mobile',
  'vr',
  'controller',
  'really',
  'lmao'],
 ['ipshita_ahsan:',
  '“seeing',
  'believing',
  'sometimes',
  'most',
  'real',
  'things',
  'world',
  'things',
  'we',
  "can't",
  'see.”',
  'tom',
  'hanks',
  'on',
  'faith'],
 ['how', 'magic', 'leap', 'lightwear', 'headset', 'might', 'actually', 'work'],
 ['even',
  'big',
  'reveal',
  'all',
  'we',
  'have',
  'go',
  'on',
  'mocked-up',
  'impressions',
  'videos...'],
 ['test',
  'pit',
  'news',
  'magic',
  'leap',
  'one',
  'mixed',
  'reality',
  'headset',
  'coming',
  'soon'],
 ['techdisease',
  'magic',
  'leap',
  'shows',
  'off',
  'magic',
  'leap',
  'one',
  '‘creator',
  'edition’',
  'ar',
  'headset',
  'shipping',
  '2018'],
 ['privacy',
  'versions',
  'keyboards',
  '10',
  'more',
  'things'

  'nypost'],
 ['magic', 'leap', 'debuts', 'augmentedreality', 'glasses', 'via', 'nypost'],
 ['roblemvr:',
  'magic',
  'leap',
  'demo',
  'exactly',
  'what',
  'ar',
  'startup',
  'didn’t',
  'need',
  'magicleap'],
 ['roblemvr:',
  'magic',
  'leap',
  'demo',
  'exactly',
  'what',
  'ar',
  'startup',
  'didn’t',
  'need',
  'magicleap'],
 ['roblemvr:',
  'magic',
  'leap',
  'demo',
  'exactly',
  'what',
  'ar',
  'startup',
  'didn’t',
  'need',
  'magicleap'],
 ['arealityevent:',
  'magic',
  'leap',
  'finally',
  'unveils',
  'augmented',
  'reality',
  'goggles',
  'says',
  'it’s',
  'shipping',
  'next',
  'year'],
 ['roblemvr:',
  'magic',
  'leap',
  'demo',
  'exactly',
  'what',
  'ar',
  'startup',
  'didn’t',
  'need',
  'magicleap'],
 ['roblemvr:',
  'magic',
  'leap',
  'demo',
  'exactly',
  'what',
  'ar',
  'startup',
  'didn’t',
  'need',
  'magicleap'],
 ['arealityevent:',
  'magic',
  'leap',
  'finally',
  'unveils',
  'augmented',
  'reality',
  'goggles'

  "edition.'"],
 ['marktabnet:',
  'secretive',
  "'mixed",
  "reality'",
  'startup',
  'finally',
  'revealed',
  'what',
  "it's",
  'been',
  'working',
  'on',
  'company',
  'says',
  'it'],
 ['this',
  'expansion',
  'pack',
  'sculpted',
  'me',
  "can't",
  'get',
  'over',
  'curvatures',
  'used',
  'magic',
  'leap',
  'hardware'],
 ['arconaico:',
  'most',
  'mysterious',
  'start-up',
  'ar',
  'magicleap',
  'industry',
  'has',
  'finally',
  'shown',
  'first',
  'glasses',
  'augmentedreality.➡️🚀👓',
  'acc'],
 ['company',
  'says',
  'will',
  'start',
  'shipping',
  'creator',
  'edition',
  'mixed',
  'reality',
  'headset',
  'called',
  'magic',
  'leap',
  'one',
  '2018',
  'price',
  'currently',
  'undisclosed'],
 ['secretive',
  "'mixed",
  "reality'",
  'startup',
  'finally',
  'revealed',
  'what',
  "it's",
  'been',
  'working',
  'on',
  'company',
  'says',
  'will',
  'start',
  'shipping',
  'creator',
  'edition',
  'mixed',
  'reality',
  'headset

In [33]:
# remove words that appeared only once
from collections import defaultdict
frequency = defaultdict(int)
for text in texts_1:
    for token in text:
        frequency[token] += 1

texts_1 = [[token for token in text if frequency[token] > 1] for text in texts_1]

pprint(texts_1)

[['people',
  'freaking',
  'out',
  'over',
  'magicleap',
  'product',
  'that',
  'almost',
  'no',
  'seen',
  'yet'],
 ['google’s',
  'magic',
  'leap',
  'just',
  'revealed',
  'an',
  'impressive',
  'demo',
  'augmented',
  'reality'],
 ['magicleap:',
  'world',
  'meet',
  'magic',
  'leap',
  'one',
  'magic',
  'leap',
  'one',
  'meet',
  'world',
  'more',
  'at'],
 ['6',
  'years',
  '$1.9',
  'billion',
  'funding',
  'secretive',
  'startup',
  'magic',
  'leap',
  'unveils',
  'product',
  'first',
  'time'],
 ['here', 'is', 'people', 'magicleap', 'one', 'ar', 'augmentedreality'],
 ['fascinating',
  'read',
  'on',
  'development',
  'mixed-reality',
  'magic',
  'leap',
  'i',
  'love',
  'reading',
  'about',
  'ways',
  'trick',
  'human',
  'brain'],
 ['6',
  'years',
  '$1.9',
  'billion',
  'secretive',
  'startup',
  'magic',
  'leap',
  'unveils',
  'smart',
  'glasses',
  'first',
  'time'],
 ['here', 'is', 'people', 'magicleap', 'one', 'ar', 'augmentedrealit

  'secret',
  'just',
  'got',
  'unveiled',
  'sounds',
  'astonishing'],
 ['roblemvr:',
  'magic',
  'leap',
  'ar',
  'headset',
  'hands-on',
  'offers',
  'details',
  'on',
  'field',
  'view',
  'weight',
  'amp;',
  'content',
  'magicleap',
  'mixedrea…'],
 ['more', 'excited', 'about', 'new', 'than', 'magic', 'leap'],
 ['appleinsider:',
  '$1.9',
  'billion',
  'seven',
  'years',
  'secretive',
  'magicleap',
  'teases',
  'lightwear',
  'ar',
  'headset'],
 ['magic', 'leap', 'going', 'out', 'on'],
 ['magicleap:',
  'world',
  'meet',
  'magic',
  'leap',
  'one',
  'magic',
  'leap',
  'one',
  'meet',
  'world',
  'more',
  'at'],
 ['magicleap:',
  'world',
  'meet',
  'magic',
  'leap',
  'one',
  'magic',
  'leap',
  'one',
  'meet',
  'world',
  'more',
  'at'],
 ['benedictevans:',
  'magic',
  'leap',
  'announces',
  'first',
  'sdk',
  'i',
  'tried',
  'this',
  'earlier',
  'this',
  'year',
  'felt',
  'rather',
  'like',
  'seeing',
  'multitouch',
  'first',
  't

  'funding',
  'secretive',
  'startup',
  'magic',
  'leap',
  'unveils',
  'product',
  'first',
  'time'],
 ['magic', 'leap', 'one', 'unveiled'],
 ['magicleap:',
  'world',
  'meet',
  'magic',
  'leap',
  'one',
  'magic',
  'leap',
  'one',
  'meet',
  'world',
  'more',
  'at'],
 ['magic',
  'leap',
  'ar',
  'headset',
  'hands-on',
  'offers',
  'details',
  'on',
  'field',
  'view',
  'weight',
  'amp;',
  'content'],
 ['futurology',
  'magic',
  'leap',
  'one',
  'just',
  'got',
  'announced',
  'early',
  '2018',
  'featuring',
  'lightfield',
  'display',
  'via',
  'r/futurology'],
 ["'magic",
  "leap'",
  'just',
  'started',
  'trending',
  '13879',
  'tweets',
  'more',
  'trends',
  'trndnl'],
 ['magic', 'leap', 'ar', 'headset', 'hands-on', 'offers', '..', '..'],
 ['magic',
  'leap',
  'shows',
  'off',
  'magic',
  'leap',
  'one',
  "'creator's",
  "edition'",
  'ar',
  'headset',
  'shipping',
  '2018',
  'by'],
 ['$1.9',
  'billion',
  'later',
  'magic',
  "lea

  'teases',
  'lightwear',
  'ar',
  'headset'],
 ['magicleap:',
  'world',
  'meet',
  'magic',
  'leap',
  'one',
  'magic',
  'leap',
  'one',
  'meet',
  'world',
  'more',
  'at'],
 ['',
  "magicleap's",
  'creator',
  'edition',
  'here',
  'looking',
  'forward',
  'all',
  'that',
  'mixedreality',
  'has',
  'offer'],
 ['bbctech:',
  'magic',
  "leap's",
  'hi-tech',
  'augmented',
  'reality',
  'glasses',
  'revealed'],
 ['magic',
  "leap's",
  'new',
  'ar',
  'headset',
  'looks',
  'promising',
  "it's",
  'going',
  'be',
  'interesting',
  'see',
  'how',
  'compares',
  "microsoft's"],
 ['my',
  'magic',
  'leap',
  'skepticism',
  'optimism',
  'explained',
  'no',
  'matter',
  'what',
  'this',
  'an',
  'important',
  'product',
  'our',
  'future',
  'marketing'],
 ['benedictevans:',
  'magic',
  'leap',
  'announces',
  'first',
  'sdk',
  'i',
  'tried',
  'this',
  'earlier',
  'this',
  'year',
  'felt',
  'rather',
  'like',
  'seeing',
  'multitouch',
  'fir

  'call',
  'me',
  'when',
  'your',
  'images',
  'opaque',
  'i',
  'already',
  'tried',
  'hololens',
  'ms',
  'showed',
  'their',
  'demos',
  'like',
  'images',
  'opaque',
  "it's",
  'super',
  'weird',
  'bad',
  'see',
  'world',
  'behind',
  'images'],
 ['magic', 'leap', 'finally', 'revealed'],
 ['magic', 'leap', 'ar', 'goggles', 'revealed'],
 ['magicleap:',
  'world',
  'meet',
  'magic',
  'leap',
  'one',
  'magic',
  'leap',
  'one',
  'meet',
  'world',
  'more',
  'at'],
 ["i've",
  'been',
  'waiting',
  'magicleap',
  'make',
  'this',
  'announcement',
  'excited',
  'about',
  'getting',
  'my',
  'hands',
  'on',
  'magic',
  'leap',
  'one',
  'magicleapone'],
 ['businessinsider:',
  '6',
  'years',
  '$1.9',
  'billion',
  'magic',
  'leap',
  'unveils',
  'ar',
  'smart-glasses'],
 ['magic',
  'leap',
  'says',
  'will',
  'ship',
  'first',
  'augmented',
  'reality',
  'glasses',
  '2018'],
 ['magic',
  'leap',
  'says',
  'will',
  'ship',
  'first',
  

...

 ['everything',
  'we',
  'know',
  'about',
  'magic',
  "leap's",
  'mysterious',
  'new',
  'headset',
  'that',
  'cost',
  '$1.9',
  'billion',
  '6',
  'years',
  'create'],
 ['businessinsider:',
  '$1.9',
  'billion',
  'later',
  'magic',
  'leap',
  'finally',
  'unveiled',
  'smart',
  'glasses',
  '—',
  "here's",
  'what',
  'we',
  'know'],
 ['everything',
  'we',
  'know',
  'about',
  'magic',
  "leap's",
  'mysterious',
  'new',
  'headset',
  'that',
  'cost',
  '$1.9',
  'billion',
  '6',
  'years',
  'create',
  'website',
  'news'],
 ['got',
  'fly',
  'stay',
  'alive',
  'these',
  'words',
  'these',
  'words',
  'no',
  'magic',
  'till',
  'we',
  'try',
  'take',
  'reach',
  'stars',
  'night',
  'break',
  'this',
  "there's",
  'up',
  'sky',
  'where',
  'love',
  'fly'],
 ['everything',
  'we',
  'know',
  'about',
  'magic',
  "leap's",
  'mysterious',
  'new',
  'headset',
  'that',
  'cost',
  '$1.9',
  'billion',
  '6'],
 ['magic', 'leap', 'unveiled',

  'instacart',
  'magic',
  'leap',
  '..',
  'looking',
  'forward',
  'updates',
  '2018',
  'thanks'],
 ['have', 'leap', 'outside', 'your', 'comfort', "that's", 'magic'],
 ['magic', 'leap', 'design'],
 ['yahoofinance:',
  'there',
  'reasons',
  'be',
  'skeptical',
  'about',
  'magic',
  "leap's",
  'long-awaited',
  'ar',
  'headset',
  'danielhowley'],
 ['6',
  'years',
  '$1.9',
  'billion',
  'secretive',
  'magic',
  'leap',
  'unveils',
  'product',
  'first',
  'time'],
 ['gazecoin:',
  "microsoft's",
  'holonlens',
  'headset',
  'has',
  'some',
  'serious',
  'competition',
  'google-backed',
  'startup',
  'magic',
  'leap',
  'has',
  'announced',
  'that',
  'their',
  'mixedr…'],
 ['magic', 'leap', 'unveiled', 'unknown'],
 ['magic', 'leap', 'stellt', 'neue', 'augmented-reality-brille', 'vor'],
 ['magic', 'leap', 'one', 'release', 'date', 'price', 'features'],
 ['can', 'magic', 'leap', 'deliver', 'on', 'big', 'hardware', 'reveal'],
 ['crunch', 'report', 'magic', 'leap

  'on',
  'mysterious',
  'mixed',
  'reality',
  'glasses'],
 ['blood', 'bone', 'behind', 'magic', 'leap', 'mixed', 'reality', 'goggles'],
 ['themalia:', 'an', 'early', 'analysis', 'magic', 'leap', 'one'],
 ['secretive',
  '‘mixed',
  'reality’',
  'startup',
  'finally',
  'revealed',
  'what',
  'it’s',
  'been',
  'working',
  'on'],
 ['cnntech:', 'magic', 'leap', 'has', 'big', 'plans', '2018'],
 ['rabovitz:',
  'vintage',
  'early',
  'magic',
  'leap',
  '-)',
  'happy',
  'holidays',
  'everyone',
  '😎😎😎'],
 ['novusprecision:',
  'jimmarous:',
  'magic',
  "leap's",
  'ar',
  'headset',
  'on',
  "it's",
  'way',
  '..',
  'big',
  'deal',
  'ar',
  'vr',
  '...'],
 ['will', 'magic', 'leap', 'take', 'privacy', 'seriously'],
 ['jimmarous:',
  'magic',
  "leap's",
  'ar',
  'headset',
  'on',
  "it's",
  'way',
  '..',
  'big',
  'deal',
  'ar',
  'vr',
  '...'],
 ['i',
  'can',
  'that',
  'that',
  '$2b',
  'magic',
  'leap',
  'headset',
  'will',
  'feel',
  'shit',
  'on',
  

  'content',
  'makers',
  'create..'],
 ['magic',
  'leap',
  'will',
  'be',
  'opening',
  'software',
  'development',
  'kit',
  'next',
  'year',
  'developers',
  'content',
  'makers',
  'create..'],
 ['i',
  'liked',
  'youtube',
  'video',
  'has',
  'tried',
  'magic',
  'leap',
  "what's",
  'like'],
 ['augmented',
  'reality',
  'goggles',
  'by',
  'magic',
  'leap',
  'unveiled',
  '',
  'shipping',
  'next',
  'year',
  'tech',
  'innovation'],
 ['magic',
  'leap',
  'unveils',
  'first',
  'ar',
  'headset',
  "that'll",
  'launch',
  '2018'],
 ['$1.9',
  'billion',
  'later',
  'magic',
  "leap's",
  'headset',
  'has',
  'same',
  'problem',
  'as',
  'microsoft',
  'hololens',
  'via',
  'sai'],
 ['magic',
  'leap',
  'gives',
  'peek',
  'hi-tech',
  'glasses',
  'ar',
  'magicleap',
  'vr'],
 ['magicleap', 'smartglasses', 'slated', '2018', 'release'],
 ['can', 'magic', 'leap', 'deliver', 'on', 'big', 'hardware', 'reveal'],
 ['magic',
  'leap',
  'finally',
  'unve

  'know',
  'our',
  'website'],
 ['magic', 'leap', 'one', 'release', 'date', 'price', 'features'],
 ['whoa',
  'that’s',
  'not',
  'what',
  'we',
  'expecting',
  'magic',
  'leap',
  'headset',
  'look',
  'like'],
 ['magic',
  'leap',
  'finally',
  'unveils',
  'augmented',
  'reality',
  'goggles',
  'says',
  'it’s',
  'shipping',
  'next',
  'year'],
 ['magic', 'leap', 'finally', 'their', 'vr', 'glasses'],
 ['rickking16:',
  'watch',
  'zed',
  'mini',
  'magic',
  'leap',
  'sairento',
  'vr',
  'arizona',
  'sunshine',
  'pimax',
  'amp;',
  'more',
  'vr',
  'roundup',
  'ep20',
  'on',
  'youtube'],
 ['like', 'magic', 'leap', 'facebook'],
 ['mattmiesnieks:',
  'great',
  'magic',
  'leap',
  'hw',
  'analysis',
  'daniel',
  'wagner',
  'one',
  'world',
  'experts',
  'this',
  'space'],
 ['magicleap:',
  'take',
  'peek',
  'behind',
  'our',
  'partnership',
  'sigurros',
  'amp;',
  'get',
  'know',
  'tónandi',
  'generative',
  'ecosystem',
  'we’re',
  'building',
 

In [34]:
# Save the mapping between id and words, known as dictionary
dictionary = corpora.Dictionary(texts_1)
dictionary.save(os.path.join(TEMP_FOLDER, 'dataset.dict'))  # store the dictionary, for future reference
print(dictionary)

2018-01-07 19:50:54,293 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2018-01-07 19:50:54,434 : INFO : built Dictionary(2279 unique tokens: ['people', 'freaking', 'out', 'over', 'magicleap']...) from 5018 documents (total 60977 corpus positions)
2018-01-07 19:50:54,436 : INFO : saving Dictionary object under C:\Users\maximjxw\AppData\Local\Temp\dataset.dict, separately None
2018-01-07 19:50:54,443 : INFO : saved C:\Users\maximjxw\AppData\Local\Temp\dataset.dict


Dictionary(2279 unique tokens: ['people', 'freaking', 'out', 'over', 'magicleap']...)


In [35]:
# Plot the number of tokens and occurances
print(dictionary.token2id)

{'people': 0, 'freaking': 1, 'out': 2, 'over': 3, 'magicleap': 4, 'product': 5, 'that': 6, 'almost': 7, 'no': 8, 'seen': 9, 'yet': 10, 'google’s': 11, 'magic': 12, 'leap': 13, 'just': 14, 'revealed': 15, 'an': 16, 'impressive': 17, 'demo': 18, 'augmented': 19, 'reality': 20, 'magicleap:': 21, 'world': 22, 'meet': 23, 'one': 24, 'more': 25, 'at': 26, '6': 27, 'years': 28, '$1.9': 29, 'billion': 30, 'funding': 31, 'secretive': 32, 'startup': 33, 'unveils': 34, 'first': 35, 'time': 36, 'here': 37, 'is': 38, 'ar': 39, 'augmentedreality': 40, 'fascinating': 41, 'read': 42, 'on': 43, 'development': 44, 'mixed-reality': 45, 'i': 46, 'love': 47, 'reading': 48, 'about': 49, 'ways': 50, 'trick': 51, 'human': 52, 'brain': 53, 'smart': 54, 'glasses': 55, '9to5google:': 56, 'google-backed': 57, 'headset': 58, 'shipping': 59, '2018': 60, 'fabled': 61, 'real': 62, "it's": 63, 'coming': 64, 'cnet': 65, "leap's": 66, 'finally': 67, 'developers': 68, 'early': 69, 'you': 70, 'can’t': 71, 'ship': 72, 'pro

In [36]:
# Convert the whole dataset into a corpus
corpus = [dictionary.doc2bow(text) for text in texts_1]
# Save the data in case we need it later
corpora.MmCorpus.serialize(os.path.join(TEMP_FOLDER, 'dataset_corpus.mm'), corpus)
# Peek it
for c in corpus:
    print(c)

2018-01-07 19:50:54,573 : INFO : storing corpus in Matrix Market format to C:\Users\maximjxw\AppData\Local\Temp\dataset_corpus.mm
2018-01-07 19:50:54,577 : INFO : saving sparse matrix to C:\Users\maximjxw\AppData\Local\Temp\dataset_corpus.mm
2018-01-07 19:50:54,581 : INFO : PROGRESS: saving document #0
2018-01-07 19:50:54,613 : INFO : PROGRESS: saving document #1000
2018-01-07 19:50:54,649 : INFO : PROGRESS: saving document #2000
2018-01-07 19:50:54,681 : INFO : PROGRESS: saving document #3000
2018-01-07 19:50:54,713 : INFO : PROGRESS: saving document #4000
2018-01-07 19:50:54,748 : INFO : PROGRESS: saving document #5000
2018-01-07 19:50:54,749 : INFO : saved 5018x2279 matrix, density=0.512% (58570/11436022)
2018-01-07 19:50:54,753 : INFO : saving MmCorpus index to C:\Users\maximjxw\AppData\Local\Temp\dataset_corpus.mm.index


[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 1), (8, 1), (9, 1), (10, 1)]
[(11, 1), (12, 1), (13, 1), (14, 1), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 1)]
[(12, 2), (13, 2), (21, 1), (22, 2), (23, 2), (24, 2), (25, 1), (26, 1)]
[(5, 1), (12, 1), (13, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1)]
[(0, 1), (4, 1), (24, 1), (37, 1), (38, 1), (39, 1), (40, 1)]
[(12, 1), (13, 1), (41, 1), (42, 1), (43, 1), (44, 1), (45, 1), (46, 1), (47, 1), (48, 1), (49, 1), (50, 1), (51, 1), (52, 1), (53, 1)]
[(12, 1), (13, 1), (27, 1), (28, 1), (29, 1), (30, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (54, 1), (55, 1)]
[(0, 1), (4, 1), (24, 1), (37, 1), (38, 1), (39, 1), (40, 1)]
[(5, 1), (12, 1), (13, 1), (27, 1), (28, 1), (29, 1), (30, 1), (31, 1), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1)]
[(12, 1), (13, 1), (19, 1), (20, 1), (34, 1), (35, 1), (56, 1), (57, 1), (58, 1), (59, 1), (60, 1)]
[(12, 2), (13, 1), (24, 1), (39, 1

[(39, 1), (43, 1), (70, 1), (103, 1), (338, 1), (374, 1), (521, 1), (1279, 1), (1280, 1), (1281, 1), (1282, 1), (1283, 1), (1284, 1), (1285, 1)]
[(12, 1), (13, 1), (39, 1), (55, 1), (64, 1)]
[(12, 1), (13, 1), (39, 1), (55, 1), (64, 1)]
[(39, 1), (40, 1), (326, 1), (501, 1), (651, 1), (1225, 1), (1254, 1), (1255, 1), (1256, 1), (1257, 1), (1258, 1), (1259, 1), (1260, 1)]
[(12, 1), (13, 1), (19, 1), (20, 1), (34, 1), (39, 1), (59, 1), (67, 1), (155, 1), (255, 1), (298, 1), (332, 1), (363, 1), (501, 1), (738, 1)]
[(39, 1), (43, 1), (70, 1), (103, 1), (338, 1), (374, 1), (521, 1), (1279, 1), (1280, 1), (1281, 1), (1282, 1), (1283, 1), (1284, 1), (1285, 1)]
[(630, 1), (1032, 1), (1127, 1), (1229, 1), (1230, 1), (1231, 1), (1232, 1), (1336, 1), (1337, 1), (1338, 1)]
[(12, 1), (39, 1), (58, 1), (60, 1), (64, 1), (106, 1), (153, 1)]
[(12, 1), (13, 1), (63, 1), (220, 1), (255, 1), (895, 1), (959, 1), (997, 1)]
[(12, 1), (39, 1), (66, 1), (70, 2), (129, 1), (137, 1), (155, 1), (193, 1), (397, 1

[(12, 2), (13, 2), (19, 2), (20, 3), (22, 1), (24, 1), (43, 1), (121, 1), (159, 1), (173, 1), (267, 1), (268, 1), (327, 1), (378, 1), (574, 1), (1137, 1), (1173, 1), (1179, 1), (1186, 1), (1758, 1), (2030, 1), (2031, 1), (2032, 1), (2033, 1), (2034, 1), (2038, 1)]
[(12, 2), (13, 2), (19, 1), (20, 1), (22, 1), (24, 1), (121, 1), (159, 1), (267, 1), (268, 1), (1186, 1), (1266, 1), (2039, 1)]
[(12, 2), (13, 2), (19, 1), (20, 1), (22, 1), (24, 1), (121, 1), (159, 1), (267, 1), (268, 1), (1186, 1)]
[(12, 2), (13, 2), (22, 1), (24, 1), (39, 1), (121, 1), (159, 1), (267, 1), (268, 1), (918, 1), (1186, 1)]
[(12, 2), (13, 2), (22, 1), (24, 1), (39, 1), (121, 1), (159, 1), (267, 1), (268, 1), (918, 1), (1186, 1)]
[(12, 2), (13, 2), (22, 1), (24, 1), (39, 1), (121, 1), (159, 1), (267, 1), (268, 1), (918, 1), (1186, 1)]
[(12, 2), (13, 2), (22, 1), (24, 1), (39, 1), (121, 1), (159, 1), (267, 1), (268, 1), (918, 1), (1186, 1)]
[(12, 2), (13, 2), (22, 1), (24, 1), (39, 1), (121, 1), (159, 1), (267, 1

### TF-IDF and similarity

In [37]:
# Load all associate libraries
from gensim import corpora, models, similarities

In [38]:
# Transform the corpus into a set of words counts (that applies weighting to account for common terms)
tfidf = models.TfidfModel(corpus) # step 1 -- initialize a model

2018-01-07 19:50:55,673 : INFO : collecting document frequencies
2018-01-07 19:50:55,677 : INFO : PROGRESS: processing document #0
2018-01-07 19:50:55,713 : INFO : calculating IDF weights for 5018 documents and 2278 features (58570 matrix non-zeros)


In [39]:
# Assume we have 12 features, then we can compact it by...
index = similarities.SparseMatrixSimilarity(tfidf[corpus], num_features=12)

2018-01-07 19:50:55,729 : INFO : creating sparse index
2018-01-07 19:50:55,733 : INFO : creating sparse matrix from corpus
2018-01-07 19:50:55,739 : INFO : PROGRESS: at document #0
2018-01-07 19:50:55,958 : INFO : created <5018x12 sparse matrix of type '<class 'numpy.float32'>'
	with 58570 stored elements in Compressed Sparse Row format>


In [40]:
corpus_tfidf = tfidf[corpus]

### Other transformation approaches

In [41]:
# Random projections
model = models.RpModel(corpus_tfidf, num_topics=2)

2018-01-07 19:50:55,994 : INFO : no word id mapping provided; initializing from corpus, assuming identity
2018-01-07 19:50:56,202 : INFO : constructing (2, 2279) random matrix


In [42]:
# Random projections
model = models.LdaModel(corpus_tfidf, id2word=dictionary, num_topics=2)

2018-01-07 19:50:56,222 : INFO : using symmetric alpha at 0.5
2018-01-07 19:50:56,226 : INFO : using symmetric eta at 0.00043878894251864854
2018-01-07 19:50:56,226 : INFO : using serial LDA version on this node
2018-01-07 19:50:56,278 : INFO : running online (single-pass) LDA training, 2 topics, 1 passes over the supplied corpus of 5018 documents, updating model once every 2000 documents, evaluating perplexity every 5018 documents, iterating 50x with a convergence threshold of 0.001000
2018-01-07 19:50:56,278 : WARNING : too few updates, training might not converge; consider increasing the number of passes or iterations to improve accuracy
2018-01-07 19:50:56,358 : INFO : PROGRESS: pass 0, at document #2000/5018
2018-01-07 19:51:00,012 : INFO : merging changes from 2000 documents into a model of 5018 documents
2018-01-07 19:51:00,045 : INFO : topic #0 (0.500): 0.013*"goggles" + 0.010*"ar" + 0.009*"reality" + 0.008*"revealed" + 0.008*"valuation" + 0.007*"top" + 0.007*"surpass" + 0.007*

In [43]:
# Hierarchical Dirichlet Process, HDP
model = models.LdaModel(corpus_tfidf, id2word=dictionary, num_topics=2)

2018-01-07 19:51:04,108 : INFO : using symmetric alpha at 0.5
2018-01-07 19:51:04,112 : INFO : using symmetric eta at 0.00043878894251864854
2018-01-07 19:51:04,112 : INFO : using serial LDA version on this node
2018-01-07 19:51:04,154 : INFO : running online (single-pass) LDA training, 2 topics, 1 passes over the supplied corpus of 5018 documents, updating model once every 2000 documents, evaluating perplexity every 5018 documents, iterating 50x with a convergence threshold of 0.001000
2018-01-07 19:51:04,155 : WARNING : too few updates, training might not converge; consider increasing the number of passes or iterations to improve accuracy
2018-01-07 19:51:04,230 : INFO : PROGRESS: pass 0, at document #2000/5018
2018-01-07 19:51:07,245 : INFO : merging changes from 2000 documents into a model of 5018 documents
2018-01-07 19:51:07,274 : INFO : topic #0 (0.500): 0.014*"one" + 0.013*"reality" + 0.011*"meet" + 0.011*"world" + 0.010*"augmented" + 0.009*"ar" + 0.008*"leap" + 0.008*"first" +

In [44]:
# Hierarchical Dirichlet Process, HDP
model = models.HdpModel(corpus_tfidf, id2word=dictionary)

2018-01-07 19:51:12,057 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,060 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,064 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,067 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,068 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,093 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,097 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,121 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,124 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,129 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,132 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,137 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,140 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,144 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,149 : WARNING : likelihood is decreasing!
2018-01-07 19:51:12,161 : WARNING : likelihood is decreasing!
2018-01-

2018-01-07 19:51:13,321 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,325 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,329 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,333 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,341 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,345 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,363 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,366 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,369 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,373 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,377 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,401 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,409 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,409 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,413 : WARNING : likelihood is decreasing!
2018-01-07 19:51:13,417 : WARNING : likelihood is decreasing!
2018-01-

2018-01-07 19:51:14,894 : WARNING : likelihood is decreasing!
2018-01-07 19:51:14,894 : WARNING : likelihood is decreasing!
2018-01-07 19:51:14,898 : WARNING : likelihood is decreasing!
2018-01-07 19:51:14,986 : WARNING : likelihood is decreasing!
2018-01-07 19:51:14,994 : WARNING : likelihood is decreasing!
2018-01-07 19:51:14,998 : WARNING : likelihood is decreasing!
2018-01-07 19:51:15,002 : WARNING : likelihood is decreasing!
2018-01-07 19:51:15,006 : WARNING : likelihood is decreasing!
2018-01-07 19:51:15,010 : WARNING : likelihood is decreasing!
2018-01-07 19:51:15,014 : WARNING : likelihood is decreasing!
2018-01-07 19:51:15,018 : WARNING : likelihood is decreasing!
2018-01-07 19:51:15,022 : WARNING : likelihood is decreasing!
2018-01-07 19:51:15,026 : WARNING : likelihood is decreasing!
2018-01-07 19:51:15,086 : WARNING : likelihood is decreasing!
2018-01-07 19:51:15,090 : WARNING : likelihood is decreasing!
2018-01-07 19:51:15,094 : WARNING : likelihood is decreasing!
2018-01-

2018-01-07 19:51:16,392 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,396 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,396 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,460 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,464 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,468 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,476 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,488 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,492 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,532 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,764 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,768 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,768 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,772 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,776 : WARNING : likelihood is decreasing!
2018-01-07 19:51:16,780 : WARNING : likelihood is decreasing!
2018-01-

2018-01-07 19:51:17,532 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,532 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,532 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,550 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,552 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,553 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,553 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,569 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,569 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,585 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,585 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,585 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,585 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,585 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,585 : WARNING : likelihood is decreasing!
2018-01-07 19:51:17,585 : WARNING : likelihood is decreasing!
2018-01-

...

2018-01-07 19:51:58,838 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,842 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,846 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,850 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,854 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,858 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,862 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,862 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,914 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,918 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,926 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,930 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,934 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,970 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,974 : WARNING : likelihood is decreasing!
2018-01-07 19:51:58,978 : WARNING : likelihood is decreasing!
2018-01-

2018-01-07 19:52:00,744 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,748 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,748 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,756 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,790 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,793 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,796 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,800 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,804 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,808 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,812 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,816 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,820 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,820 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,824 : WARNING : likelihood is decreasing!
2018-01-07 19:52:00,864 : WARNING : likelihood is decreasing!
2018-01-

2018-01-07 19:52:01,949 : WARNING : likelihood is decreasing!
2018-01-07 19:52:01,953 : WARNING : likelihood is decreasing!
2018-01-07 19:52:01,957 : WARNING : likelihood is decreasing!
2018-01-07 19:52:01,961 : WARNING : likelihood is decreasing!
2018-01-07 19:52:01,965 : WARNING : likelihood is decreasing!
2018-01-07 19:52:01,965 : WARNING : likelihood is decreasing!
2018-01-07 19:52:01,973 : WARNING : likelihood is decreasing!
2018-01-07 19:52:02,032 : WARNING : likelihood is decreasing!
2018-01-07 19:52:02,036 : WARNING : likelihood is decreasing!
2018-01-07 19:52:02,039 : WARNING : likelihood is decreasing!
2018-01-07 19:52:02,039 : WARNING : likelihood is decreasing!
2018-01-07 19:52:02,043 : WARNING : likelihood is decreasing!
2018-01-07 19:52:02,051 : WARNING : likelihood is decreasing!
2018-01-07 19:52:02,055 : WARNING : likelihood is decreasing!
2018-01-07 19:52:02,055 : WARNING : likelihood is decreasing!
2018-01-07 19:52:02,059 : WARNING : likelihood is decreasing!
2018-01-

2018-01-07 19:52:03,284 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,289 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,293 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,296 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,337 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,345 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,353 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,357 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,361 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,409 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,413 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,421 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,425 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,429 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,429 : WARNING : likelihood is decreasing!
2018-01-07 19:52:03,469 : WARNING : likelihood is decreasing!
2018-01-

2018-01-07 19:52:04,574 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,578 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,583 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,598 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,602 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,606 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,622 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,626 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,634 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,638 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,642 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,646 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,688 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,691 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,694 : WARNING : likelihood is decreasing!
2018-01-07 19:52:04,697 : WARNING : likelihood is decreasing!
2018-01-

#### This is the end of part 4 Data Cleaning & Topic Analysis